# Gaussian Processes

## 1. Introduction

### 1.1 Abstract

In supervised learning, we often rely on __parametric methods__ of the form $p({\bf y} \mid {\bf X}, {\bf w})$ to explain and predict data, inferring the optimal values of __parameters__ ${\bf w}$ via methods such as maximum likelihood estimation (MLE). But there are problems with this approach.

One problem is that this requires us to choose a functional form and fixed number of weights in advance &#151; for example, an order-3 polynomial $ax^2 + bx + c$ with weights ${\bf w} = \begin{bmatrix} a & b & c \end{bmatrix}$. This means our model is highly constrained to a specific functional form and we have a fixed number of weights for data of various complexity, so it's important to choose sensibly. 

However, what if we don't have sufficient prior knowledge to choose the functional form? This motivates an alternative approach to Bayesian regression, which is this:

> Instead of weights, shouldn't we deal with functions directly?

This is, in a nutshell, the thinking behind __non-parametric methods__, of which __Gaussian processes__ are one. Instead of inferring a distribution over parameters, Gaussian processes are used to infer a probability distribution $p(F)$ over functions directly. The Gaussian process can then be fit to data and used to make predictions and measure the confidence of those predictions.

In this article, we'll first revise the fundamentals of multivariate normal distributions (MVNs), the core component of Gaussian processes; introduce Gaussian processes; and see how Gaussian processes can be applied to regression.

### 1.2 Contents
1. Introduction
2. Getting Started
3. Multivariate Normal (MVN)
4. Gaussian Processes
5. Covariance Functions
6. Gaussian Process Regression
7. Sources

## 2. Getting Started

#### For Colab Users
You'll need to first grab the `requirements.txt` from the [GitHub](https://github.com/meganelisabethfinch/ai503-article), double check the path is correct and run the cell below.

![Colab Instructions](https://raw.githubusercontent.com/meganelisabethfinch/ai503-article/main/colab-requirements.png)

In [ ]:
!pip install -r '/requirements.txt'

#### For All Users
The examples in this notebook make use of additional libraries and the plotting functions defined below. Make sure you have installed the requirements, and then run this cell once to import modules and define utility functions before continuing.

In [1]:
import numpy as np
import matplotlib.pyplot as plt
import GPy

GPy.plotting.change_plotting_library('plotly')
# GPy's built-in plotly implementation is broken due to deprecated functions. :(
# This might give a warning but please ignore it.
# As I define my own plotting functions below.

import plotly.graph_objects as go
from plotly.subplots import make_subplots

from scipy.stats import multivariate_normal
from scipy.stats import norm
from numpy.linalg import inv

# FOR PLOTTING 2D GAUSSIANS (SECTION 3)
# Palette for Plotly heatmap
heatmapHex = ["#46049f", "#7202a8", "#9c189d", "#bc3886", "#d8576c", "#ed7953", "#fb9e3a", "#fdca27", "#f0f91f"]

def invert_block_matrix(Sigma, blocks=True):
    '''
    Utility function to invert a block matrix, to get the precision matrix Lambda from covariance matrix Sigma.
    
    Args:
        Sigma -- square input matrix to invert
        blocks -- return the individual blocks instead
    '''
    r, h = Sigma.shape
    # In general, we want nrows=ncols=number of variables in x1.
    # For now, we'll just split in half.
    nrows, ncols = int(r / 2), int(h / 2)
    A, B, C, D = (Sigma.reshape(h//nrows, nrows, -1, ncols)
                 .swapaxes(1, 2)
                 .reshape(-1, nrows, ncols))
    Aprime = inv(A - B @ inv(D) @ C)
    
    Lambda11 = Aprime
    Lambda12 = - Aprime @ B @ inv(D)
    Lambda21 = - inv(D) @ C @ Aprime
    Lambda22 = inv(D) + inv(D) @ C @ Aprime @ B @ inv(D)
    
    if blocks:
        return Lambda11, Lambda12, Lambda21, Lambda22
    
    return np.block([
        [Lambda11, Lambda12],
        [Lambda21, Lambda22]
    ])
    

def plotly_2DGaussian(xaxis_range, yaxis_range, mu, cov, conditional=False, conditional_cut=None, res=60):
    '''
    Plot a 2D Gaussian distribution as a heatmap, along with its marginal (or conditional distributions).
    
    Args:
        xaxis_range -- the lowest and highest value to display on the x-axis in the form [xmin, xmax]
        yaxis_range -- as above for y
        mu -- the mean vector [mu1, mu2]
        cov -- the 2x2 covariance matrix
        conditional -- plot marginals if False, or conditionals if True
        conditional_cut -- to display the conditional distribution p(x1 | x2), we must fix the value of x2
            i.e. we actually display p(x1 | x2 = a).
            We will similarly display p(x2 | x1 = b).
            Hence, conditional_cut = [a, b], the points at which we take the cut.
        res -- resolution i.e. number of points to sample between [xmin, xmax]
    '''
    xmin, xmax = xaxis_range[0], xaxis_range[1]
    ymin, ymax = yaxis_range[0], yaxis_range[1]
    
    x1 = np.linspace(xmin, xmax, res)[:, None]
    x2 = np.linspace(ymin, ymax, res)[:, None]
    x1_grid, x2_grid = np.meshgrid(x1, x2)

    # Pack X1, X2 into a single 3-dimensional array
    pos = np.dstack((x1_grid, x2_grid))
    rv_joint = multivariate_normal(mu, Sigma)

    marginal_size = 0.18 # The size of the marginal plot, in relation to the main plot
    fig = make_subplots(rows=2, cols=2, shared_xaxes=True, shared_yaxes=True, vertical_spacing = 0.02, horizontal_spacing=0.02, row_heights=[marginal_size,1-marginal_size], column_widths=[1-marginal_size, marginal_size])

    # Plot 2D Gaussian
    fig.add_trace(go.Contour(
        z=rv_joint.pdf(pos),
        x=x1.ravel(), # horizontal axis
        y=x2.ravel(), # vertical axis
        showscale=False,
        contours_showlines=False
    ), row=2, col=1)

        
    if not conditional:
        rv_marginal_1 = norm(mu[0], Sigma[0][0]) # x1 ~ N(mu1, Sigma11)
        rv_marginal_2 = norm(mu[1], Sigma[1][1]) # x2 ~ N(mu2, Sigma22)
        
        # Plot 1D Gaussian marginals
        fig.add_trace(go.Scatter(x=x1.ravel(), y=rv_marginal_1.pdf(x1.ravel()), name="p(x1)", line=go.scatter.Line(color=heatmapHex[1])), row=1, col=1)
        fig.add_trace(go.Scatter(y=x2.ravel(), x=rv_marginal_2.pdf(x2.ravel()), name="p(x2)", line=go.scatter.Line(color=heatmapHex[3])), row=2, col=2)
        
        # Update axes
        fig.update_yaxes(title="p(x1)", row=1, col=1)
        fig.update_xaxes(title="p(x2)", row=2, col=2)
        fig.update_layout(title_text="Marginalisation")
    else:
        Lambda11, Lambda12, Lambda21, Lambda22 = invert_block_matrix(cov, blocks=True)
        
        # p(x1 | x2) ~ N(mu1 - inv(Lambda11) Lambda12(x2 - mu2), inv(Lambda11))
        mu_cond_1 = mu[0] - inv(Lambda11) @ Lambda12 * (conditional_cut[0] - mu[1])
        cov_cond_1 = inv(Lambda11)
        # Univariate dist expects scalar mean and cov, so extract from the 1x1 matrix
        # OK because this function is explicitly for 2D Gaussians (not 3D+)
        rv_cond_1 = norm(mu_cond_1[0][0], cov_cond_1[0][0])
        
        # As above, flipping 1s and 2s
        # p(x2 | x1) ~ N(mu2 - inv(Lambda22) Lambda21(x1 - mu1), inv(Lambda22))
        mu_cond_2 = mu[1] - inv(Lambda22) @ Lambda21 * (conditional_cut[1] - mu[0])
        cov_cond_2 = inv(Lambda22)
        rv_cond_2 = norm(mu_cond_2[0][0], cov_cond_2[0][0])
        
        # Plot 1D Gaussian conditionals
        fig.add_trace(go.Scatter(x=x1.ravel(), y=rv_cond_1.pdf(x1.ravel()), name="p(x1 | x2 = {a})".format(a=conditional_cut[0]), line=go.scatter.Line(color=heatmapHex[1])), row=1, col=1)
        fig.add_trace(go.Scatter(y=x2.ravel(), x=rv_cond_2.pdf(x2.ravel()), name="p(x2 | x1 = {b})".format(b=conditional_cut[1]), line=go.scatter.Line(color=heatmapHex[3])), row=2, col=2)
        
        # Plot fixed values of x1, x2 ('cuts')
        fig.add_hline(y=conditional_cut[0], annotation_text="x2={x2}".format(x2=conditional_cut[0]), annotation_font_size=20, annotation_font_color="black", line_width=2, line_dash="dash", line_color="black", row=2, col=1)
        fig.add_vline(x=conditional_cut[1], annotation_text="x1={x1}".format(x1=conditional_cut[1]), annotation_font_size=20, annotation_font_color="black", line_width=2, line_dash="dash", line_color="black", row=2, col=1)
        
        # Update axes
        fig.update_yaxes(title="p(x1 | x2)", row=1, col=1)
        fig.update_xaxes(title="p(x2 | x1)", row=2, col=2)
        fig.update_layout(title_text="Conditionalisation")
    
    fig.update_layout(height=800, width=800)
    fig.update_xaxes(title="x1", range=[xmin, xmax], row=2, col=1)
    fig.update_yaxes(title="x2", range=[ymin, ymax], row=2, col=1)
    marginal_tick_distance = 0.2
    fig.update_yaxes(range=[0., 1.], dtick=marginal_tick_distance, row=1, col=1)
    fig.update_xaxes(range=[0., 1.], dtick=marginal_tick_distance, row=2, col=2)
    fig.show()

# Palette from Matplotlib
colorsHex = {\
    "black": "#000000",\
    "darkBlue": "#204a87",\
    "blue": "#1f77b4",\
    "orange": "#ff7f0e",\
    "green": "#2ca02c",\
    "red": "#d62728",\
    "purple": "#9467bd",\
    "brown": "#8c564b",\
    "yellow": "#bcbd22",\
    "pink": "#e377c2",\
    "teal": "#17becf"}

# Unique colours defined for first 7 plots, then we cycle through
colorWheel = ["orange", "green", "red", "purple", "pink", "yellow", "teal"]
meanColor = colorsHex["blue"]

def hex2rgb(hexcolor):
    hexcolor = [hexcolor[1+2*i:1+2*(i+1)] for i in range(3)]
    r,g,b = [int(n,16) for n in hexcolor]
    return (r,g,b)

def plotly_fill_between(ax, X, lower, upper, color=colorsHex['blue'], label=None, hide_legend=False, line_kwargs=None, **kwargs):
    if not 'line' in kwargs:
        kwargs['line'] = go.scatter.Line(**line_kwargs or {})
    else:
        kwargs['line'].update(line_kwargs or {})
        
    if color.startswith('#'):
        fcolor = 'rgba({c[0]}, {c[1]}, {c[2]}, {alpha})'.format(c=hex2rgb(color), alpha=0.1)
    else:
        fcolor = color
        
    u = go.Scatter(x=X, y=upper, fill='tonextx', fillcolor=fcolor, showlegend=(not hide_legend) and label is not None, name=label, legendgroup='{}_fill_({},{})'.format(label, ax[0], ax[1]), **kwargs)
    l = go.Scatter(x=X, y=lower, fillcolor=fcolor, showlegend=False, name=label, legendgroup='{}_fill_({},{})'.format(label, ax[0], ax[1]), **kwargs)
    return l, u

def plotly_gp(mu, cov, X, X_train=None, Y_train=None, samples=[], title=""):
    '''
    Plot a Gaussian process using plotly.
    
    Args:
        mu -- the mean vector
        cov -- the covariance matrix
        X -- the grid of X values
        X_train, Y_train -- the training data i.e. any points with known values, to be plotted as scatter points.
        samples -- samples (functions) drawn from the Gaussian process.
    '''
    fig = go.Figure(layout=go.Layout(hovermode='x'))
    fig.update_layout(title_text=title)
    
    X = np.squeeze(X)
    mu = np.squeeze(mu)
    
    # Plot confidence interval as shaded area
    uncertainty = 1.96 * np.sqrt(np.diag(cov))
    confidence_line = {'color': colorsHex['darkBlue'], 'width': 0.5 }
    l, u = plotly_fill_between((fig.layout.xaxis, fig.layout.yaxis), X, mu - uncertainty, mu + uncertainty, label="Confidence", line_kwargs=confidence_line)
    fig.add_trace(l)
    fig.add_trace(u)
    
    # Plot mean
    fig.add_trace(go.Scatter(x=X, y=mu, name='Mean', line=go.scatter.Line(color=meanColor)))
    
    # Plot samples
    for i, sample in enumerate(samples):
        line_color = colorsHex[colorWheel[i % len(colorWheel)]]
        fig.add_trace(go.Scatter(x=X, y=samples[i], name=f'Sample {i+1}', line=go.scatter.Line(color=line_color)))
    
    # Plot training data, if any
    if X_train is not None and Y_train is not None:
        fig.add_trace(go.Scatter(x=X_train.ravel(), y=Y_train.ravel(), mode='markers', marker=dict(color=colorsHex['black'], symbol='x'), name='Data'))
    
    fig.show()
    
def plotly_gps(data=[], nrows=1, ncols=1, title=""):
    '''
    Plot several Gaussian processes together as subplots.
    Plots are similar in style to plotly_gp but share a single legend.
    
    Args:
        data -- a dict/object including the args to plotly i.e. mu, cov, X, and optionally X_train, Y_train, samples, etc...
        nrows, ncols -- the dimensions of the subplot grid, s.t. nrows * ncols <= len(data)
        title -- the main title of the figure
    '''
    titles = [subplot_data['title'] if 'title' in subplot_data else None for subplot_data in data]
    fig = make_subplots(rows=nrows, cols=ncols, subplot_titles=titles)
    fig.update_layout(title_text=title, hovermode='x')
    
    for r in range(nrows):
        for c in range(ncols):
            subplot_data = data[r * ncols + c]
            mu = np.squeeze(subplot_data['mu'])
            cov = subplot_data['cov']
            X = np.squeeze(subplot_data['X'])
            X_train = subplot_data['X_train'] if 'X_train' in subplot_data else None
            Y_train = subplot_data['Y_train'] if 'Y_train' in subplot_data else None
            samples = subplot_data['samples'] if 'samples' in subplot_data else []
            
            showlegend = r == 0 and c == 0
            
            # Plot confidence
            uncertainty = 1.96 * np.sqrt(np.diag(cov))
            confidence_line = {'color': colorsHex['darkBlue'], 'width': 0.5 }
            # Pass (0,0) as axes for shared legend group across all subplots
            l, u = plotly_fill_between((0,0), X, mu - uncertainty, mu + uncertainty, label="Confidence", hide_legend = not showlegend, line_kwargs=confidence_line)
            fig.add_trace(l, row=r+1, col=c+1)
            fig.add_trace(u, row=r+1, col=c+1)
            
            # Plot mean
            fig.add_trace(go.Scatter(x=X, y=mu, name='Mean', legendgroup='Mean', showlegend=showlegend, line=go.scatter.Line(color=meanColor)), row=r+1, col=c+1)

            # Plot samples
            for i, sample in enumerate(samples):
                line_color = colorsHex[colorWheel[i % len(colorWheel)]]
                fig.add_trace(go.Scatter(x=X, y=samples[i], name=f'Sample {i+1}', legendgroup=f'Sample {i+1}', showlegend=showlegend, line=go.scatter.Line(color=line_color)), row=r+1, col=c+1)

            # Plot training
            if X_train is not None and Y_train is not None:
                fig.add_trace(go.Scatter(x=X_train.ravel(), y=Y_train.ravel(), legendgroup='Data', showlegend=showlegend, mode='markers', marker=dict(color=colorsHex['black'], symbol='x'), name='Data'), row=r+1, col=c+1)
    fig.show()

def plotly_kernels(X, Zs, subtitles=[], title="", nrows=1, ncols=1):
    fig = make_subplots(rows=nrows, cols=ncols, subplot_titles=subtitles)
    fig.update_layout(title_text=title)
    
    xmin, xmax = min(X.ravel()), max(X.ravel())
    
    for r in range(nrows):
        for c in range(ncols):
            Z = Zs[r * ncols + c]
            showscale = r == 0 and c == 0
            fig.add_trace(go.Heatmap(x=X.ravel(), y=X.ravel(), z=Z, showscale=showscale), row=r+1, col=c+1)

    fig.show()
    

 /Users/meganfinch/Documents/Projects/ai503-article/venv/lib/python3.7/site-packages/plotly/graph_objs/_deprecations.py:385: DeprecationWarning:plotly.graph_objs.Line is deprecated.
Please replace it with one of the following more specific types
  - plotly.graph_objs.scatter.Line
  - plotly.graph_objs.layout.shape.Line
  - etc.



## 3. Multivariate Normal (MVN)

### 3.1 Definition

We will first introduce the _multivariate normal (MVN) distribution_, the key ingredient in Gaussian processes. We write $\mathbf{x} \sim \mathcal{N} (\boldsymbol{\mu}, \boldsymbol{\Sigma})$ to indicate that a random variable $\mathbf{x}$ is Gaussian distributed with mean vector $\boldsymbol{\mu}$ and covariance matrix $\boldsymbol{\Sigma}$. This random variable also has probability density function

$$ p(\mathbf{x}) = \frac{1}{\sqrt{(2 \pi)^d | \boldsymbol{\Sigma} |}} \exp \Big( -\frac{1}{2} ({\bf x} - \boldsymbol{\mu})^\top \boldsymbol{\Sigma}^{-1} ({\bf x} - \boldsymbol{\mu}) \Big) $$

If we rewrite ${\bf x}$, $\boldsymbol{\mu}$ and $\boldsymbol{\Sigma}$ as
$$ {\bf x} = \begin{bmatrix} {\bf x}_1 \\ {\bf x}_2 \end{bmatrix} \quad \boldsymbol{\mu} = \begin{bmatrix} \boldsymbol{\mu}_1 \\ \boldsymbol{\mu}_2 \end{bmatrix} \quad \boldsymbol{\Sigma} = \begin{bmatrix} \boldsymbol{\Sigma}_{11} & \boldsymbol{\Sigma}_{12} \\ \boldsymbol{\Sigma}_{21} & \boldsymbol{\Sigma}_{22} \end{bmatrix} $$

we see that $\mathbf{x}_1$ and $\mathbf{x}_2$ are random variables whose joint distribution in Gaussian — that is, $p({\bf x}) = p({\bf x}_1, {\bf x}_2)$.  We are interested in determining $p({\bf x}_1)$ and $p({\bf x}_1 \mid {\bf x}_2)$. In this section, we will discuss how these can be found through _marginalisation_ and _conditioning_, and how Gaussian processes are closed under these two operations.

### 3.2 Marginals

$p({\bf x}_1)$ is the result of marginalisation.

We won't write the full proof here, but it is possible to show that

$$ p({\bf x}_1) = \mathcal{N} (\boldsymbol{\mu}_1 , \boldsymbol{\Sigma}_{11}) $$

The code block below visualises the results of marginalisation, by plotting a 2D Gaussian $p({\bf x})$ (centre) along with the marginal distributions $p({\bf x}_1)$ (top) and $p({\bf x}_2)$ (right). The mean and covariance matrix can be altered to alter the plot below.

In [2]:
# Plot 2D Gaussian with its marginals

# Vary the mean and covariance and rerun this block to change the plot 
mu = np.array([0.5, -0.2])
Sigma = np.array([[2.0, 0.3], [0.3, 0.5]])

plotly_2DGaussian([-3, 3], [-3, 3], mu=mu, cov=Sigma)
                  

### 3.3 Conditionals

We can derive $p({\bf x}_1 \mid {\bf x}_2)$ by conditioning. 

To do this, we additionally define the precision matrix to be the inverse of the covariance matrix

$$ \boldsymbol{\Lambda} = \boldsymbol{\Sigma}^{-1} = \begin{bmatrix} \boldsymbol{\Lambda}_{11} & \boldsymbol{\Lambda}_{12} \\ \boldsymbol{\Lambda}_{21} & \boldsymbol{\Lambda}_{22} \end{bmatrix} $$

Note that this constrains our covariance matrix to be invertible. Writing $\boldsymbol{\Sigma}$ as

$$ \boldsymbol{\Sigma} = \begin{bmatrix} {\bf A} & {\bf B} \\ {\bf C} & {\bf D} \end{bmatrix} $$

it is possible to show that

$$ \boldsymbol{\Lambda}_{11} = {\bf A}' $$
$$ \boldsymbol{\Lambda}_{12} = - {\bf A}' {\bf B} {\bf D}^{-1} $$
$$ \boldsymbol{\Lambda}_{21} = - {\bf D}^{-1} {\bf C} {\bf A}' $$
$$ \boldsymbol{\Lambda}_{22} = {\bf D}^{-1} + {\bf D}^{-1} {\bf C} {\bf A}' {\bf B} {\bf D}^{-1} $$

where ${\bf A}' = ({\bf A} - {\bf B}{\bf D}^{-1} {\bf C})^{-1}$. The inversion of a block matrix is implemented in `invert_block_matrix(...)` in Section 2. We won't write the full proof here, but, having defined $\boldsymbol{\Lambda}$, it is possible to show that

$$ p({\bf x}_1 \mid {\bf x}_2 ) = \mathcal{N} (\boldsymbol{\mu}_1 - \boldsymbol{\Lambda}_{11}^{-1} \boldsymbol{\Lambda}_{12} (\mathbf{x}_2 - \boldsymbol{\mu}_2 ) , \boldsymbol{\Lambda}_{11}^{-1}) $$

The code block below visualises the results of conditioning, by plotting a 2D Gaussian $p({\bf x})$ (centre) along with the conditional distributions $p({\bf x}_1 \mid {\bf x}_2)$ (top) and $p({\bf x}_2 \mid {\bf x}_1)$ (right). In order to visualise this, we need to 'fix' the condition values &#151; so what is _actually_ plotted is $p({\bf x}_1 \mid {\bf x}_2 = a)$ and $p({\bf x}_2 \mid {\bf x}_2 \mid {\bf x}_1 = b)$. The 'cut' values $a$ and $b$ can be altered, along with the mean and covariance matrix, to alter the plot below.

In [3]:
# Plot 2D Gaussian with its conditionals

# Vary the mean and covariance and rerun this block to change the plot 
mu = np.array([0.5, -0.2])
Sigma = np.array([[2.0, 0.3], [0.3, 0.5]])
cut_values = [-2., 0.]

plotly_2DGaussian([-3, 3], [-3, 3], mu=mu, cov=Sigma, conditional=True, conditional_cut=cut_values)

## 4. Gaussian Processes

### 4.1 Intuition

Now that we've recapped some important properties of mutlivariate Gaussian distributions, we are ready to introduce Gaussian processes. Formally, a Gaussian process is defined as:

> A set of random variables forms a _Gaussian process_ if any finite subset of them is _jointly Gaussian distributed_.

What does this definition actually mean? First, let's consider functions $f : \mathbb{R} \rightarrow \mathbb{R}$. Note that $\mathbb{R}$, is an infinite, uncountable set. We can define a random variable for every $x \in \mathbb{R}$ in the domain and hence form the set ${\bf x} = \{ {\rm rv}(x) \mid x \in \mathbb{R} \}$. Please note the use of ${\rm rv}(x)$ to counter a slight abuse of notation: the locations $x$ of the domain are _fixed_; the actual random variable is $Y$, for which we wish to predict a particular value $Y = y$. However, it's common to write ${\bf x}_i$ to indicate the random variable corresponding to that location. 

If we assume the distribution of ${\bf x}$ to be the multivariate normal $\mathbf{x} \sim \mathcal{N}(\boldsymbol{\mu}, \boldsymbol{\Sigma})$, for appropriate $\boldsymbol{\mu}$ and $\boldsymbol{\Sigma}$, then the set ${\bf x}$ forms a Gaussian process. In particular, the distribution of this Gaussian process is the joint distribution ${\bf x} \sim \mathcal{N}(\boldsymbol{\mu}, \boldsymbol{\Sigma})$ of these infinitely many random variables, which is therefore a distribution over functions $f$ defined on $\mathbb{R}$.

In practice, it is impractical to work with infinitely many random variables. Therefore, as in Section 3.1, we rewrite ${\bf x}$ as

$$ {\bf x} = \begin{bmatrix} {\bf x}_1 \\ {\bf x}_2 \end{bmatrix} $$

where ${\bf x}_1$ is a finite subset of ${\bf x}$ and ${\bf x}_2 = {\bf x} \setminus {\bf x}_1$. Informally, ${\bf x}_1$ is _"anything we care about"_ and ${\bf x}_2$ is _"everything we don't"_. This typically translates to ${\bf x}_1$ being the training data points or additional points we wish to predict. Then, because Gaussian distributions are closed under marginalisation, we marginalise out ${\bf x}_2$ to get a distribution ${\bf x}_1 \sim \mathcal{N}(\boldsymbol{\mu}_1, \boldsymbol{\Sigma}_{11})$ over just ${\bf x}_1$. 

This motivates the above definition of a Gaussian process: if every such finite subset ${\bf x}_1 \subset {\bf x}$ of a set ${\bf x}$ is jointly Gaussian distributed, then ${\bf x}$ forms a Gaussian process. 

### 4.2 Definition

We can extend the above intuition to functions $f : \mathbb{R}^d \rightarrow \mathbb{R}$. To specify a Gaussian process on vectors in $\mathbb{R}^d$, we just need
1. A mean function $m : \mathbb{R}^d \rightarrow \mathbb{R}$
2. A covariance function $k : \mathbb{R}^d \times \mathbb{R}^d \rightarrow \mathbb{R}$

$$ m({\bf x}) = \mathbb{E}_{f \sim F} [ f({\bf x}) ] $$
$$ k({\bf x}_1, {\bf x}_2) = \mathbb{E}_{f \sim F} [(f ({\bf x}_1) - m ({\bf x}_1)) (f ({\bf x}_2) - m({\bf x}_2)) ] $$

We then write

$$ F \sim {\rm GP}(m,k) $$

to denote that $F$ is a Gaussian process. 

By specifying $m$ and $k$, we can get different kinds of function $f$ when sampling from $F$. In general, it is assumed that $m({\bf x}) = 0$, as we can always shift the data so that it has zero-mean (a process called _centering_) and add the mean back in later. But the choice of covariance function is much more important.

## 5. Covariance Functions

A covariance function or kernel $k : \mathbb{R}^d \times \mathbb{R}^d \rightarrow \mathbb{R}$ returns for two points ${\bf x}_1, {\bf x}_2 \in \mathbb{R}^d$ a scalar value representing the degree of similarity between those points. The _covariance matrix_ $\Sigma$ (also known as the _Gram matrix_) is formed by applying this kernel to all pairs $({\bf x}_i, {\bf x}_j)$ from our finite set of random variables. There is only really one requirement for a valid kernel, which is that the resulting covariance matrix $\Sigma$ should be positive definite (and hence symmetric and invertible).

In this section, we will introduce several common covariance functions and see how the choice of covariance kernel changes the characteristics of the functions $f \sim {\rm GP}(m,k)$ sampled from our GP, without specifying a rigid form.

### 5.1. (Some) Common Covariance Functions

__Polynomial__

The polynomial kernel is
$$ k({\bf x}_1, {\bf x}_2) = \sigma_f^2 (c + l {\bf x}_1^\top {\bf x}_2)^k $$

with hyperparameters $\sigma_f^2$ (the overall variance), $l$ (the lengthscale), $c$ (the bias) and $k$ (the order).

__Exponential__

The exponential kernel is
$$ k({\bf x}_1, {\bf x}_2) = \sigma_f^2 \exp \Big( -\frac{|{\bf x}_1 - {\bf x}_2|}{l}\Big)$$


__Squared exponential (RBF)__

The squared exponential kernel, better known as the radial basis function, is defined as

$$ k({\bf x}_1, {\bf x}_2) = \sigma_f^2 \exp \Big( - \frac{|{\bf x}_1 - {\bf x}_2|^2}{2l^2} \Big)$$


__Gamma exponential__

Another form of the exponential kernel is the $\gamma$-exponential kernel, defined as

$$ k({\bf x}_1, {\bf x}_2) = \exp \Big( - \Big( \frac{|{\bf x}_1 - {\bf x}_2 |}{l} \Big)^\gamma \Big) $$

with additional hyperparameter $\gamma$.

__Rational quadratic__

The rational quadratic kernel is defined as
$$ k({\bf x}_1, {\bf x}_2) = \sigma_f^2 \Big( 1 + \frac{|{\bf x}_1 - {\bf x}_2|^2}{2 \alpha l^2} \Big)^{-\alpha} $$

with additional hyperparameter $\alpha$ (the scale-mixture $\alpha > 0$).

__Neural network__

The neural network kernel is
$$ k({\bf x}_1, {\bf x}_2) = \sigma^2 \frac{2}{\pi} {\rm asin}\Big( \frac{ \sigma_w^2 {\bf x}_1^\top {\bf x}_2 + \sigma_b^2 }{\sqrt{\sigma_w^2 {\bf x}_1^\top {\bf x}_1 + \sigma_b^2 + 1} \sqrt{\sigma_w^2 {\bf x}_2^\top  {\bf x}_2 + \sigma_b^2 + 1 }} \Big) $$

with hyperparameters $\sigma_f^2$ (the overall variance), $\sigma_w^2$ (the variance in the weights) and $\sigma_b^2$ (the variance in the bias).

### 5.2 Classifying Covariance Functions

Note that several of these functions contain a common expression, $|{\bf x}_1 - {\bf x}_2|$. One way of classifying covariance functions is, in fact, whether or not they can be rewritten as a function of ${\bf r} = |{\bf x}_1 - {\bf x}_2|$.

Covariance functions that can be expressed as a function $k({\bf r})$ are called _stationary_, because they depend only on the relative positions of two points (i.e. their distance) and hence are invariant to translations. RBF, the rational quadratic and the other exponential kernels are all stationary kernels.

_Non-stationary_ kernels, such as the neural network and polynomial kernel, can incorporate the absolute positions of ${\bf x}_1$ and ${\bf x}_2$.

Code for these covariance functions is given below.

In [4]:
# HELPER FUNCTIONS
def squared_dist(x1,x2):
    return np.sum(x1**2, 1).reshape(-1,1) + np.sum(x2**2, 1) - 2 * np.dot(x1,x2.T)

def comp_prod(X1, weight_variance, bias_variance, X2=None):
    if X2 is None:
        return (np.square(X1)*weight_variance).sum(axis=1)+bias_variance
    else:
        return (X1 * weight_variance).dot(X2.T)+bias_variance

# DEFINE KERNELS
def poly_kernel(x1, x2, l=1., c=1., sigma=1., k=3.):
    '''
    Polynomial kernel, as defined above.
    
    Args:
        x1 -- array of m points (m x d)
        x2 -- array of n points (n x d)
        l -- scale or length parameter
        c -- bias
        sigma -- defines the variance, sigma**2
        k -- order
    '''
    dot_prod = np.dot(x1, x2.T)
    A = (l * dot_prod) + c
    B = A ** k
    return (sigma**2) * B
    
def exp_kernel(x1, x2, sigma_f=1., l=1.):
    '''
    Exponential kernel, as defined above.
    
    Args:
        x1 -- array of m points (m x d)
        x2 -- array of n points (n x d)
        sigma_f -- defines variances
        l -- length or smoothness parameter
    '''
    return (sigma_f**2) * np.exp(- np.sqrt(squared_dist(x1,x2)) / l)
    
def rbf(x1, x2, l=1.0, sigma_f=1.0):
    '''
    RBF or squared exponential kernel, as defined above. 
    
    Args:
        x1 -- array of m points (m x d)
        x2 -- array of n points (n x d)
        l -- length or smoothness parameter
        sigma_f -- defines the variance, sigma_f**2
        
    Returns:
        (m x n) matrix
    '''
    return sigma_f**2 * np.exp(-0.5 / l**2 * squared_dist(x1, x2))

def gamma_exp(x1, x2, l=.5, gamma=.5):
    '''
    Gamma exponential kernel, as defined above.
    
    Args:
        x1 -- array of m points (m x d)
        x2 -- array of n points (n x d)
        l -- length or smoothness parameter
        gamma
    '''
    return np.exp(- (squared_dist(x1, x2) / l)**gamma)

def rational_quadratic(x1, x2, sigma_f=1., l=3., alpha=3.):
    '''
    Rational quadratic kernel, as defined above.
    
    Args:
        x1 -- array of m points (m x d)
        x2 -- array of n points (n x d)
        l -- length or smoothness parameter
        alpha --
    '''
    return (1 + ( (squared_dist(x1, x2) ) / (2 * alpha * l**2) ) )**(-alpha)

def neural_network(x1, x2, sigma=1., sigma_w=1., sigma_b=1.):
    '''
    Neural network kernel, as defined above. Also known as the arc sine or MLP kernel.
    
    Args:
        x1 -- array of m points (m x d)
        x2 -- array of n points (n x d)
        sigma -- defines the variance sigma**2
        sigma_w -- defines variance sigma_w**2 of prior over input weights
        sigma_b -- define variance sigma_b**2 of prior over bias parameters
    '''
    numer = comp_prod(x1, sigma_w**2, sigma_b**2, x2)
    x1_denom = np.sqrt( comp_prod(x1, sigma_w**2, sigma_b**2) + 1.)
    x2_denom = np.sqrt( comp_prod(x2, sigma_w**2, sigma_b**2) + 1.)
    fraction = numer / x1_denom[:, None] / x2_denom[None, :]
    asin = np.arcsin(fraction)
    return sigma**2 * (2. / np.pi) * asin

Next, let's see what these kernels look like for $N=25$ evenly spaced points between $-5$ and $5$.

In [5]:
# What do these kernels look like?
X = np.linspace(-5, 5, 25)[:, None]

# 1. RBF or Squared Exponential
l_rbf, sigma_f_rbf = .5, 1.
rbf_cov = rbf(X,X,l=l_rbf, sigma_f=sigma_f_rbf)
rbf_title = "Squared Exponential (RBF) (\u03C3_f={sigma_f}, l={l})".format(l=l_rbf, sigma_f=sigma_f_rbf)

# 2. Gamma Exponential
l_gam, gamma = .5, .5
gamma_cov = gamma_exp(X, X, l = l_gam, gamma=gamma)
gamma_title = "Gamma Exponential (l={l}, \u03B3={gamma})".format(l=l_gam, gamma=gamma)

# 3. Rational Quadratic
sigma_f_rq, l_rq, alpha = 1., 3., 3.
rq_cov = rational_quadratic(X, X, sigma_f=sigma_f_rq, l=l_rq, alpha=alpha)
rq_title = "Rational Quadratic (\u03C3_f={sigma_f}, l={l}, \u03B1={alpha})".format(sigma_f=sigma_f_rq, l=l_rq, alpha=alpha)

# 4. Neural Network
sigma_nn, sigma_w, sigma_b = 1., 3.5, 3
nn_cov = neural_network(X, X, sigma=sigma_nn, sigma_w=sigma_w, sigma_b=sigma_b)
nn_title = "Neural Network (\u03C3={sigma}, \u03C3_w={sigma_w}, \u03C3_b={sigma_b})".format(sigma=sigma_nn, sigma_w=sigma_w, sigma_b=sigma_b)

# 5. Exponential
sigma_f_exp, l_exp = 1., 1.
exp_cov = exp_kernel(X, X, sigma_f=sigma_f_exp, l=l_exp)
exp_title = "Exponential (\u03C3_f={sigma_f}, l={l})".format(sigma_f=sigma_f_exp, l=l_exp)

# 6. Polynomial
l_poly, k, sigma_poly, c = 1., 3., 1., 1.
poly_cov = poly_kernel(X, X, l=l_poly, c=c, sigma=sigma_poly, k=k)
poly_title = "Polynomial (\u03C3_f={sigma}, l={l}, k={order}, c={c})".format(sigma=sigma_poly, l=l_poly, order=k, c=c)

subtitles = [rbf_title, gamma_title, rq_title, nn_title, exp_title, poly_title]
small_subtitles = ['<span style="font-size: 12px;">' + subtitle + '</span>' for subtitle in subtitles]
plotly_kernels(X, [rbf_cov, gamma_cov, rq_cov, nn_cov, exp_cov, poly_cov], subtitles=small_subtitles, title="Covariance Kernels", nrows=2, ncols=3)


Next, let's see how the choice of covariance kernel affects the characteristics of the functions $f$ drawn from the GP. The cell below randomly samples $N = 3$ functions $f$ from the Gaussian process prior (no training data is used) $\mathcal{N}(\boldsymbol{\mu}, \boldsymbol{\Sigma})$, with mean $\boldsymbol{\mu} = {\bf 0}$ and $\boldsymbol{\Sigma}$ formed from each kernel above.

In [6]:
# What do functions drawn from these kernels look like?
# Plot priors
NSAMPLES = 3
X = np.linspace(-5., 5., 500)[:, None]
mu = np.zeros((500))

# 1. RBF or Squared Exponential
rbf_cov = rbf(X,X,l=l_rbf, sigma_f=sigma_f_rbf)
rbf_samples = np.random.multivariate_normal(mu, rbf_cov, NSAMPLES)

# 2. Gamma Exponential
gamma_cov = gamma_exp(X, X, l = l_gam, gamma=gamma)
gamma_samples = np.random.multivariate_normal(mu, gamma_cov, NSAMPLES)

# 3. Rational Quadratic
rq_cov = rational_quadratic(X, X, sigma_f=sigma_f_rq, l=l_rq, alpha=alpha)
rq_samples = np.random.multivariate_normal(mu, rq_cov, NSAMPLES)

# 4. Neural Network
nn_cov = neural_network(X, X, sigma=sigma_nn, sigma_w=sigma_w, sigma_b=sigma_b)
nn_samples = np.random.multivariate_normal(mu, nn_cov, NSAMPLES)

# 5. Exponential
exp_cov = exp_kernel(X, X, sigma_f=sigma_f_exp, l=l_exp)
exp_samples = np.random.multivariate_normal(mu, exp_cov, NSAMPLES)

# 6. Polynomial
poly_cov = poly_kernel(X, X, l=l_poly, c=c, sigma=sigma_poly, k=k)
poly_samples = np.random.multivariate_normal(mu, poly_cov, NSAMPLES)

# View the prior plots in a grid for comparison
subplot_data = [{'mu': mu, 'cov': rbf_cov, 'X': X, 'samples': rbf_samples, 'title': rbf_title}, {'mu': mu, 'cov': gamma_cov, 'X':X, 'samples': gamma_samples, 'title': gamma_title}, {'mu': mu, 'cov': rq_cov, 'X': X, 'samples': rq_samples, 'title': rq_title}, {'mu': mu, 'cov': nn_cov, 'X': X, 'samples': nn_samples, 'title': nn_title}, {'mu': mu, 'cov': exp_cov, 'X':X, 'samples':exp_samples, 'title':exp_title}, {'mu': mu, 'cov': poly_cov, 'X':X, 'samples':poly_samples, 'title':poly_title}]
plotly_gps(subplot_data, 3, 2, title="Gaussian Process Priors")



Uncomment the `plotly_gp` calls below to take a closer look at the prior plots above.

In [7]:
# UNCOMMENT THESE TO TAKE A CLOSER LOOK AT ONE OF THE PRIOR PLOTS ABOVE.
plotly_gp(mu, rbf_cov, X, samples=rbf_samples, title=rbf_title)
# plotly_gp(mu, gamma_cov, X, samples=gamma_samples, title=gamma_title)
# plotly_gp(mu, rq_cov, X, samples=rq_samples, title=rq_title)
# plotly_gp(mu, nn_cov, X, samples=nn_samples, title=nn_title)
# plotly_gp(mu, exp_cov, X, samples=exp_samples, title=exp_title)
# plotly_gp(mu, poly_cov, X, samples=poly_samples, title=poly_title)

## 6. Gaussian Process Regression

Let's now explore one use case for Gaussian processes, which is non-linear regression. We want to use the Gaussian process to make predictions about the values of our function between the training data (_interpolation_) and beyond (_extrapolation_). 

To do this, we'll first learn how to fit our Gaussian process (and hyperparameters) to the training data. We'll then use the fitted model (_posterior_) to make predictions. And, along the way, we'll see how to implement this both from first principles (using `numpy`) and using the Gaussian process library `GPy` from the University of Sheffield's ML group.

### 6.1. Fitting a Gaussian Process

#### Prior Distribution
Say we have some training data

$$ y_i = f({\bf x}_i) $$

for $i = 1, \dots, m$ and $f \sim {\rm GP}(m,k)$. For now, we will assume a zero mean (but it is also easy to incorporate a non-zero mean) and form the Gaussian process _prior_

$$ p({\bf y}) = \mathcal{N}({\bf 0}, {\bf K}) $$

where ${\bf K}_{ij} = k({\bf x}_i, {\bf x}_j)$. 

To make predictions with our Gaussian process, we will need to incorporate a point ${\bf x}_*$ for which we wish to predict the value $y_*$. How can we do this?


#### Prior to Joint Distribution
In Section 3.2, we introduced _marginalisation_ &#151; extracting a marginal distribution $p({\bf x}_1) = \mathcal{N}(\boldsymbol{\mu}_1, \boldsymbol{\Sigma}_{11})$ from a joint distribution 

$$p({\bf x}) = p({\bf x}_1, {\bf x}_2) = \mathcal{N} \Big( \begin{bmatrix} \boldsymbol{\mu}_1 \\ \boldsymbol{\mu}_2 \end{bmatrix}, \begin{bmatrix} \boldsymbol{\Sigma}_{11} & \boldsymbol{\Sigma}_{12} \\ \boldsymbol{\Sigma}_{21} & \boldsymbol{\Sigma}_{22} \end{bmatrix} \Big)$$

In this case, we know the covariance function, which allows us to compute the off-diagonal elements $\boldsymbol{\Sigma}_{12}$ and $\boldsymbol{\Sigma}_{21}$, which enables us to do the reverse process. Specifically, we obtain the __joint distribution__

$$ p(y^*, {\bf y}) = \mathcal{N}({\bf 0}, {\bf K'}) $$

where we define $k_{**} = k({\bf x}^*, {\bf x}^*) + \sigma^2$ to be the self-covariance of the prediction point; ${\bf k}_*^\top = \begin{bmatrix} k({\bf x}^*, {\bf x}_1 ) & \dots & k({\bf x}^*, {\bf x}_m)\end{bmatrix}$ to be the covariance of the prediction point with each training point; and finally

$$ {\bf K}' = \begin{bmatrix} k_{**} & {\bf k}_*^\top \\ {\bf k}_* & {\bf K} + \sigma^2 {\bf I} \end{bmatrix} = \begin{bmatrix} k_{**} & {\bf k}_*^\top \\ {\bf k}_* & {\bf L} \end{bmatrix} $$

All we have done here is expand the covariance matrix by an extra row and column to include our new prediction point, and (optionally) include some noise $\sigma^2$. 

#### Joint to Conditional Distribution
From the joint distribution, we can easily obtain the __conditional distribution__ by conditioning. Applying the formulae from Section 3.3, we obtain

$$ p(y^* \mid {\bf y}) = \mathcal{N} ({\bf k}^\top {\bf L}^{-1} {\bf y} , k - {\bf k}^\top {\bf L}^{-1} {\bf k} ) $$

#### Posterior Distribution

We'll make just one more change to obtain our __posterior distribution__, which is to extend it to an arbitrary number of prediction points.

$$ p({\bf y}^* \mid {\bf y}) = \mathcal{N} ( {\bf K}_*^\top {\bf L}^{-1} {\bf y} , {\bf K}_{**} - {\bf K}_*^\top {\bf L}^{-1} {\bf K}_*) $$

This process is implemented in the function `posterior` below, which returns the mean ${\bf \mu}_*$ and covariance $\boldsymbol{\Sigma}*$ of the posterior distribution.

In [8]:
# posterior function adapted from http://krasserm.github.io/2018/03/19/gaussian-processes/
# adjusted to support arbitrary kernel and hyperparameters

from numpy.linalg import inv

def posterior(X_s, X_train, Y_train, kernel, sigma_y=1e-8, params=None):
    '''
    Compute the statistics (mu, cov) of the posterior distribution,
    from m training data (X_train, Y_train) and n new inputs Xp.
    
    Args:
        X_s -- new input locations (n x d)
        X_train -- training location (m x d)
        Y_train -- training targets (m x 1)
        kernel -- kernel function with the form kernel(X1, X2, **kwargs)
        sigma_y -- noise parameter
        params -- misc parameters for the kernel in dictionary form.
            The key must match the named arguments.
            e.g. { 'l': 1.0, 'sigma_f': 1.0 }
    '''
    if params is not None:
        # K is L = K + sigma**2 I in the equations above
        K = kernel(X_train, X_train, **params) + sigma_y**2 * np.eye(len(X_train))
        K_s = kernel(X_train, X_s, **params) # K_s is K*
        K_ss = kernel(X_s, X_s, **params) + 1e-8 * np.eye(len(X_s)) # K_ss is K**
    else:
        K = kernel(X_train, X_train) + sigma_y**2 * np.eye(len(X_train))
        K_s = kernel(X_train, X_s)
        K_ss = kernel(X_s, X_s) + 1e-8 * np.eye(len(X_s))
    K_inv = inv(K)
    
    mu_s = K_s.T.dot(K_inv).dot(Y_train)
    cov_s = K_ss - K_s.T.dot(K_inv).dot(K_s)
    
    return mu_s, cov_s

### 6.2. Predicting with a Gaussian Process

Having obtained the posterior, predicting with a Gaussian process is very simple. The prediction $y^*$ at each point ${\bf x}^*$ is _just the mean_, but we can also contextualise this prediction by visualising the uncertainty region and drawing functions $f$ from the posterior $\mathcal{N}(\boldsymbol{\mu}^*, \boldsymbol{\Sigma}^*)$. In a noise-free model, the uncertainty is reduced to zero at training points and all functions $f$ drawn from the posterior pass through the training points.

This is visualised below, with the ground truth $y = \sin (x)$.

In [9]:
# Generate noise-free training data
X = np.linspace(-5., 5., 500)[:, None]

TRAIN_SIZE = 5
X_train = np.random.uniform(-5., 5, (TRAIN_SIZE, 1))
Y_train = np.sin(X_train)

# Compute mean and covariance of posterior
params = {'l': 1., 'sigma_f':1. }
mup, covp = posterior(X, X_train, Y_train, kernel=rbf, params=params)

# Draw samples from posterior
NSAMPLES = 3
samples = np.random.multivariate_normal(mup.ravel(), covp, NSAMPLES)
plotly_gp(mup, covp, X, X_train=X_train, Y_train=Y_train, samples=samples, title="Posterior from Noise-Free Training Data")

We can also incorporate noise into our training data. When noise is included, the uncertainty at the training points is non-zero and not all sample functions pass through the training points precisely.

In [10]:
# Generate noisy training data
X = np.linspace(-5., 5., 500)[:, None]

NOISE = 0.2
TRAIN_SIZE = 7
X_train = np.random.uniform(-5., 5, (TRAIN_SIZE, 1))
Y_train = np.sin(X_train) + NOISE * np.random.rand(*X_train.shape)

# Compute mean and covariance of posterior
mup, covp = posterior(X, X_train, Y_train, kernel=rbf, sigma_y=NOISE)

# Draw samples from posterior
NSAMPLES = 3
samples = np.random.multivariate_normal(mup.ravel(), covp, NSAMPLES)
plotly_gp(mup, covp, X, X_train=X_train, Y_train=Y_train, samples=samples, title="Posterior from Noisy Training Data")

We can also implement Gaussian process regression using the Gaussian process library `GPy`. This is fairly straightforward, except that `GPy`'s default behaviour is to assume the noise rate is unknown and try to estimate it from the training data. Therefore, to replicate the above results, we need to fix the noise rate with `model.Gaussian_noise.variance.fix()`.

In [11]:
# Compare with GPy

# Generate noisy training data
X = np.linspace(-5., 5., 500)[:, None]

NOISE = 0.2
TRAIN_SIZE = 7
X_train = np.random.uniform(-5., 5, (TRAIN_SIZE, 1))
Y_train = np.sin(X_train) + NOISE * np.random.rand(*X_train.shape)

# Compute posterior with NumPy implementation
mup1, covp1 = posterior(X, X_train, Y_train, kernel=rbf, sigma_y=NOISE)

# Compute posterior with GPy
kernel = GPy.kern.RBF(input_dim=1, variance=1., lengthscale=1.)
model = GPy.models.GPRegression(X_train, Y_train, kernel)

# GPy tries to estimate noise by default, so to reproduce the above result, we need to fix the variance
model.Gaussian_noise.variance = NOISE**2
model.Gaussian_noise.variance.fix()

mup2, covp2 = model.predict(X, full_cov=True)

# Plot side by side
subplot_data = [{'mu': mup1, 'cov': covp2, 'X': X, 'X_train': X_train, 'Y_train': Y_train, 'samples': [], 'title': "NumPy Implementation"}, {'mu': mup2, 'cov': covp2, 'X':X, 'X_train': X_train, 'Y_train': Y_train, 'samples': [], 'title': "GPy Implementation"}]
plotly_gps(subplot_data, 1, 2, title="Gaussian Process Posteriors")

### 6.2 Hyperparameters

In Section 1.1, we introduced Gaussian processes as a way to eliminate weights and deal with functions directly, reformulating problem of the form $p({\bf w} \mid {\bf y})$ as $p(f \mid {\bf y})$. While it's true we've eliminated weights, we _haven't_ eliminated all hyperparameters. Therefore, we still need a sensible approach to picking hyperparameters.

#### 6.2.1 Effect of Hyperparameters

First, we'll briefly look at the effect hyperparameters have on the shape of the random functions $f$. The cell below visualises just the RBF kernel with hyperparameters $\sigma_f = [1, 10]$ and $l = [0.5, 1]$. Clearly, $\sigma_f$ controls the variance (effective range of the function) and $l$ the smoothness.

In [12]:
# Plot priors
NSAMPLES = 3
X = np.linspace(-5., 5., 500)[:, None]
mu = np.zeros((500))

rbf_parameters = [(0.5, 1), (1, 1), (0.5, 10), (1, 10)]
subplot_data = []

for l1, sigma_f in rbf_parameters:
    rbf_cov = rbf(X,X,l=l1, sigma_f=sigma_f)
    rbf_samples = np.random.multivariate_normal(mu, rbf_cov, NSAMPLES)
    rbf_title = "Squared Exponential (RBF) (\u03C3_f={sigma_f}, l={l})".format(l=l1, sigma_f=sigma_f)
    subplot_data.append({'mu': mu, 'cov': rbf_cov, 'X': X, 'samples': rbf_samples, 'title': rbf_title})
    
plotly_gps(subplot_data, 2, 2, title="Gaussian Process Priors")


#### 6.2.2 Learning Hyperparameters

Fortunately, the way Gaussian processes are formulated gives us a nice expression we can use to pick parameters. In Section 6.1, we arrived at an expression for the posterior Gaussian process, by applying conditioning

$$ p(y' \mid {\bf y}) = \frac{p(y', {\bf y})}{p({\bf y})}$$

Clearly, we can also incorporate the hyperparameters ${\bf p}$ (parameters associated with the covariance function $k({\bf x}_1, {\bf x}_2)$ and the noise rate $\sigma^2$), so we have

$$ p(y' \mid {\bf y}, {\bf p}) = \frac{p(y',{\bf y} \mid {\bf p}) }{p ({\bf y} \mid {\bf p}) }$$

The denominator of this expression is the marginal likelihood, of the training data with respect to the hyperparameters,

\begin{equation} p({\bf y} \mid {\bf p}) = \mathcal({\bf 0}, {\bf L}) = \frac{1}{\sqrt{(2 \pi)^m |L| }} \exp \Big( -\frac{1}{2} {\bf y}^\top {\bf L}^{-1} {\bf y} \Big)  \end{equation}

but, as usual, it is easier to work with the $\log$ marginal likelihood

\begin{equation*}
\log p({\bf y} \mid {\bf p}) = -\frac{1}{2} \log |{\bf L}| - \frac{1}{2} {\bf y}^\top {\bf L}^{-1} {\bf y} - \frac{m}{2} \log 2\pi
\end{equation*}

So, we can optimise our hyperparameters by minimising the _negative log likelihood_. This is implemented in the functions `nll_fn` and `optimise` below.

In [13]:
# Optimising Hyper-parameters (Pt 1)
# nll_fn function adapted from http://krasserm.github.io/2018/03/19/gaussian-processes/
# adjusted to support arbitrary kernel and hyperparameters

from numpy.linalg import cholesky, det
from scipy.linalg import solve_triangular
from scipy.optimize import minimize
    
def nll_fn(X_train, Y_train, sigma_y, kernel, params=None, naive=True):
    '''
    Returns a function that computes the negative log marginal likelihood
    for training data (X_train, Y_train), given noise level and kernel.
    
    Args:
        X_train -- training locations (m x d)
        Y_train -- training targets (m x 1)
        sigma_y -- noise parameter
        kernel --
        params -- ordered list of keyword hyperparameters,
            aligned with theta. For example,
                ['l', 'sigma_f']
            means that l=theta[0], sigma_f=theta[1] is passed to the kernel.
        
    Returns:
        Minimisation objective.
    '''
    
    Y_train = Y_train.ravel()
    
    def nll_naive(theta):
        packed_params = { params[i] : theta[i] for i in range(0, len(theta)) }
        
        K = kernel(X_train, X_train, **packed_params) + \
            sigma_y**2 * np.eye(len(X_train))
        return 0.5 * np.log(det(K)) + \
            0.5 * Y_train.dot(inv(K).dot(Y_train)) + \
            0.5 * len(X_train) * np.log(2 * np.pi)

    def nll_stable(theta):
        packed_params = { params[i] : theta[i] for i in range(0, len(theta)) }
        
        K = kernel(X_train, X_train, **packed_params) + \
            sigma_y**2 * np.eye(len(X_train))
        L = cholesky(K)
        
        S1 = solve_triangular(L, Y_train, lower=True)
        S2 = solve_triangular(L.T, S1, lower=False)
        
        return np.sum(np.log(np.diagonal(L))) + \
            0.5 * Y_train.dot(S2) + \
            0.5 * len(X_train) * np.log(2 * np.pi)
    
    if naive:
        return nll_naive
    else:
        return nll_stable
    
def optimise(X_train, Y_train, sigma_y, kernel, params):
    names, initial_values = list(params.keys()), list(params.values())
    bounds = tuple((1e-5, None) for name in names)
    res = minimize(nll_fn(X_train, Y_train, sigma_y, kernel, params=names), initial_values, bounds=bounds, method='L-BFGS-B')
    optimised_values = res.x
    return { names[i] : optimised_values[i] for i in range(0, len(names)) }

The cell below shows the effect of optimising the hyperparameters. Note that the `plotly` functions automatically select the plot scale to suit the data, so check the $y$ axis to verify the results; the optimised result should have reduced uncertainty.

In [14]:
# Optimising Hyperparameters (Pt 2)

# Generate noisy training data
X = np.linspace(-5., 5., 500)[:, None]

NOISE = 0.2
X_train = np.arange(-3, 4, 1).reshape(-1, 1)
Y_train = np.sin(X_train) + NOISE * np.random.rand(*X_train.shape)

initial_params = {'l': 1.0, 'sigma_f': 1.0}

mup1, covp1 = posterior(X, X_train, Y_train, kernel=rbf, sigma_y=NOISE, params=initial_params)
unopt_subplot_data = {'mu': mup1, 'cov': covp1, 'X': X, 'X_train': X_train, 'Y_train': Y_train, 'title': 'Unoptimised (l={l}, \u03C3_f={sigma_f})'.format(l=initial_params['l'], sigma_f=initial_params['sigma_f'])}

# Optimise parameters in NumPy implementation
optimised_params = optimise(X_train, Y_train, NOISE, rbf, initial_params)
mup2, covp2 = posterior(X, X_train, Y_train, kernel=rbf, sigma_y=NOISE, params=optimised_params)
opt_subplot_data = {'mu': mup2, 'cov': covp2, 'X':X, 'X_train':X_train, 'Y_train':Y_train, 'title':'Optimised (l={l:.2f}, \u03C3_f={sigma_f:.2f})'.format(l=optimised_params['l'], sigma_f=optimised_params['sigma_f'])}

subplot_data = [unopt_subplot_data, opt_subplot_data]
plotly_gps(subplot_data, 1, 2, title="Gaussian Process Posteriors")

## 7. GP Regression Playground

Finally, here is a simple Gaussian process implemented in `GPy` to play with. You can try and change the number of training points (`TRAIN SIZE`), noise level (`NOISE`), number of samples to draw from the posterior (`NSAMPLES`) as well as the kernel by choosing from the documentation. The rest of the code implements the regression process, with the hyperparameters of the `GPy` implementation tuned by `model.optimise()`.

Thank you for reading. :-)

In [15]:
# GP REGRESSION PLAYGROUND
## Choose number of training points
TRAIN_SIZE = 5 
## Choose noise level
NOISE = 0.05 
## Choose number of samples to draw from posterior
NSAMPLES = 3

## Choose how test points are chosen
X_train = np.random.uniform(-5., 5, (TRAIN_SIZE, 1))
## Choose the ground truth function (or load in data)
Y_train = np.sin(np.pi*X_train/2) + np.random.randn(TRAIN_SIZE, 1) * NOISE
## Choose prior kernel
kernel = GPy.kern.RBF(input_dim=1, variance=1., lengthscale=1.)

## The rest
model = GPy.models.GPRegression(X_train, Y_train, kernel)
model.constrain_positive('')
model.optimize(messages=False) # Change to True to see optimisation output
Xp = np.linspace(-5., 5., 500)[:, None]
mup, covp = model.predict(Xp, full_cov=True)
posteriorYp = model.posterior_samples_f(Xp, full_cov=True, size=NSAMPLES)
samples = np.transpose(np.squeeze(posteriorYp)) # Reshape samples to form expected by plotting function
plotly_gp(mup, covp, Xp, X_train=X_train, Y_train=Y_train, samples=samples, title="GP Regression Playground")


## 7. Sources

- AI503 Notes
- Krasser, M. (2018) [Gaussian Processes](http://krasserm.github.io/2018/03/19/gaussian-processes/)
- Roelants, P. [Gaussian Processes (3/3) - Exploring Kernels](https://peterroelants.github.io/posts/gaussian-process-kernels/)
- [GPy Docs](https://gpy.readthedocs.io/en/deploy/GPy.kern.html) for more covariance kernels.